### The PyTorch to ONNX Conversion

In [ ]:
# Some standard imports
import torch
import torch.onnx
import onnx
import onnxruntime
import torchvision.models as models
import numpy as np

In [ ]:
model = models.mobilenet_v2(pretrained=True)
model.eval()

In [ ]:
batch_size = 1
# Input to the model
x = torch.randn(batch_size, 3, 224, 224, requires_grad=True)
torch_out = model(x)

# Export the model
torch.onnx.export(model,                     # model being run
                  x,                         # model input (or a tuple for multiple inputs)
                  "mobilenet_v2.onnx",      # where to save the model (can be a file or file-like object)
                  export_params=True,        # store the trained parameter weights inside the model file
                  opset_version=10,          # the ONNX version to export the model to
                  do_constant_folding=True,  # whether to execute constant folding for optimization
                  input_names = ['input'],   # the model's input names
                  output_names = ['output'], # the model's output names
                  dynamic_axes={'input' : {0 : 'batch_size'},    # variable length axes
                                'output' : {0 : 'batch_size'}})

In [ ]:
onnx_model = onnx.load("mobilenet_v2.onnx")
onnx.checker.check_model(onnx_model)

In [ ]:
ort_session = onnxruntime.InferenceSession("mobilenet_v2.onnx")

def to_numpy(tensor):
    return tensor.detach().cpu().numpy() if tensor.requires_grad else tensor.cpu().numpy()

# compute ONNX Runtime output prediction
ort_inputs = {ort_session.get_inputs()[0].name: to_numpy(x)}
ort_outs = ort_session.run(None, ort_inputs)

# compare ONNX Runtime and PyTorch results
np.testing.assert_allclose(to_numpy(torch_out), ort_outs[0], rtol=1e-03, atol=1e-05)

print("Exported model has been tested with ONNXRuntime, and the result looks good!")

### Running the MobileNetV2 IR on the NCS2

The following code is adapted from one of the provided OpenVINO image classification demos.

In [ ]:
"""
 Copyright (c) 2018-2021 Intel Corporation

 Licensed under the Apache License, Version 2.0 (the "License");
 you may not use this file except in compliance with the License.
 You may obtain a copy of the License at

      http://www.apache.org/licenses/LICENSE-2.0

 Unless required by applicable law or agreed to in writing, software
 distributed under the License is distributed on an "AS IS" BASIS,
 WITHOUT WARRANTIES OR CONDITIONS OF ANY KIND, either express or implied.
 See the License for the specific language governing permissions and
 limitations under the License.
"""
from __future__ import print_function
import sys
import os
import cv2
import numpy as np
import logging as log
from openvino.inference_engine import IECore
import ngraph as ng


In [ ]:
model = "mobilenet_v2.xml"
device = 'MYRIAD'
log.basicConfig(format="[ %(levelname)s ] %(message)s", level=log.INFO, stream=sys.stdout)
log.info("Loading Inference Engine")
ie = IECore()

In [ ]:
# ---1. Read a model in OpenVINO Intermediate Representation (.xml and .bin files) or ONNX (.onnx file) format ---
log.info(f"Loading network:\n\t{model}")
net = ie.read_network(model=model)

In [ ]:
# -----------------------------------------------------------------------------------------------------

# ------------- 2. Load Plugin for inference engine and extensions library if specified --------------
log.info("Device info:")
versions = ie.get_versions(device)
print(f"{' ' * 8}{device}")
print(f"{' ' * 8}MKLDNNPlugin version ......... {versions[device].major}.{versions[device].minor}")
print(f"{' ' * 8}Build ........... {versions[device].build_number}")

In [ ]:

# -----------------------------------------------------------------------------------------------------

# --------------------------- 3. Read and preprocess input --------------------------------------------
input = 'car.png'
for input_key in net.input_info:
    if len(net.input_info[input_key].input_data.layout) == 4:
        n, c, h, w = net.input_info[input_key].input_data.shape
        
images = np.ndarray(shape=(n, c, h, w))
images_hw = []
for i in range(n):
    image = cv2.imread(input)
    ih, iw = image.shape[:-1]
    images_hw.append((ih, iw))
    log.info("File was added: ")
    log.info(f"        {input}")
    if (ih, iw) != (h, w):
        log.warning(f"Image {input} is resized from {image.shape[:-1]} to {(h, w)}")
        image = cv2.resize(image, (w, h))
    # BGR to RGB
    image = cv2.cvtColor(image, cv2.COLOR_BGR2RGB)
    # Change data layout from HWC to CHW 
    image = image.transpose((2, 0, 1))  
     # Change to (0,1)
    image = image / 255. 
    # Subtract mean
    image -= np.array([0.485, 0.456, 0.406]).reshape(3,1,1)
    image /= np.array([0.229, 0.224, 0.225]).reshape(3,1,1)
    images[i] = image        

In [ ]:
# -----------------------------------------------------------------------------------------------------

# --------------------------- 4. Configure input & output ---------------------------------------------
# --------------------------- Prepare input blobs -----------------------------------------------------
log.info("Preparing input blobs")
assert (len(net.input_info.keys()) == 1 or len(
    net.input_info.keys()) == 2), "Sample supports topologies only with 1 or 2 inputs"
out_blob = next(iter(net.outputs))
for input_key in net.input_info:
    input_name = input_key
    net.input_info[input_key].precision = 'FP32'
    break

data = {}
data[input_name] = images

In [ ]:
# -----------------------------------------------------------------------------------------------------

# --------------------------- Performing inference ----------------------------------------------------
log.info("Loading model to the device")
exec_net = ie.load_network(network=net, device_name=device)
log.info("Creating infer request and starting inference")
res = exec_net.infer(inputs=data)

In [ ]:
log.info("Processing output blob")
log.info(f"Top 10 results: ")
labels_map = []
with open('mobilenet_v2.labels', 'r') as f:
    for line in f:
        labels_map += [line.strip('\n')]
classid_str = "label"
probability_str = "probability"
for i, probs in enumerate(res[out_blob]):
    probs = np.squeeze(probs)
    top_ind = np.argsort(probs)[-10:][::-1]
    print(f"Image {input}\n")
    print(classid_str, probability_str)
    print(f"{'-' * len(classid_str)} {'-' * len(probability_str)}")
    for id in top_ind:
        det_label = labels_map[id] if labels_map else f"{id}"
        label_length = len(det_label)
        space_num_before = (7 - label_length) // 2
        space_num_after = 7 - (space_num_before + label_length) + 2
        print(f"{det_label} ... {probs[id]:.7f} %")
    print("\n")